In [1]:
import itertools
import librosa
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
from scipy.stats import kurtosis
from scipy.stats import skew

In [2]:
def get_features(y, sr, n_fft=1024, hop_length=512):
    features = {}

    features['spectral_centroid'] = librosa.feature.spectral_centroid(y=y, sr=sr, n_fft=n_fft, hop_length=hop_length).ravel()
    features['spectral_rolloff'] = librosa.feature.spectral_rolloff(y=y, sr=sr, n_fft=n_fft, hop_length=hop_length).ravel()
    features['zero_crossing_rate'] = librosa.feature.zero_crossing_rate(y, frame_length=n_fft, hop_length=hop_length).ravel()
    features['rms'] = librosa.feature.rms(y=y, frame_length=n_fft, hop_length=hop_length).ravel()
    features['onset_strength'] = librosa.onset.onset_strength(y=y, sr=sr).ravel()
    features['spectral_contrast'] = librosa.feature.spectral_contrast(y=y, sr=sr).ravel()
    features['spectral_bandwidth'] = librosa.feature.spectral_bandwidth(y=y, sr=sr, n_fft=n_fft, hop_length=hop_length).ravel()
    features['spectral_flatness'] = librosa.feature.spectral_flatness(y=y, n_fft=n_fft, hop_length=hop_length).ravel()

    mfcc = librosa.feature.mfcc(y=y, n_fft = n_fft, hop_length = hop_length, n_mfcc=13)

    for index, v_mfcc in enumerate(mfcc):
        features['mfcc_{}'.format(index)] = v_mfcc.ravel()

    def get_moments(descriptors):
        result = {}

        for k, v in descriptors.items():
            result['{}_max'.format(k)] = np.max(v)
            result['{}_min'.format(k)] = np.min(v)
            result['{}_mean'.format(k)] = np.mean(v)
            result['{}_std'.format(k)] = np.std(v)
            result['{}_kurtosis'.format(k)] = kurtosis(v)
            result['{}_skew'.format(k)] = skew(v)

        return result

    additional_features = get_moments(features)
    additional_features['tempo'] = librosa.feature.tempo(y=y, sr=sr)[0]

    return additional_features

In [3]:
def process_genres_directory_files(genres_directory, genres):
    all_features = []

    for genre in genres:
        genre_directory = f'{genres_directory}/{genre}/wav_files'

        for file in os.listdir(genre_directory):
            file_path = f"{genre_directory}/{file}"

            y, sr = librosa.load(file_path)

            features = get_features(y, sr)

            features['label'] = genre

            all_features.append(features)

    return all_features

In [4]:
genres_directory = './our-music'

In [5]:
genres = os.listdir(genres_directory)

In [6]:
genres

['forro', 'funk', 'mpb', 'pop', 'rock', 'samba', 'sertanejo']

In [7]:
%%time

all_features = process_genres_directory_files(genres_directory, genres)

CPU times: total: 14min 58s
Wall time: 16min 13s


In [8]:
all_features

[{'spectral_centroid_max': 6396.12803299473,
  'spectral_centroid_min': 758.0855874725147,
  'spectral_centroid_mean': 2497.8471165806923,
  'spectral_centroid_std': 778.4580113955616,
  'spectral_centroid_kurtosis': 4.642042731607789,
  'spectral_centroid_skew': 1.5760852835101309,
  'spectral_rolloff_max': 9883.740234375,
  'spectral_rolloff_min': 1012.060546875,
  'spectral_rolloff_mean': 5572.59963658572,
  'spectral_rolloff_std': 1544.649657322049,
  'spectral_rolloff_kurtosis': 0.5118604338180246,
  'spectral_rolloff_skew': 0.28742624134882844,
  'zero_crossing_rate_max': 0.5966796875,
  'zero_crossing_rate_min': 0.0,
  'zero_crossing_rate_mean': 0.11278541021671827,
  'zero_crossing_rate_std': 0.0646446834865587,
  'zero_crossing_rate_kurtosis': 11.529737969273267,
  'zero_crossing_rate_skew': 2.5896631453423526,
  'rms_max': 0.4224141,
  'rms_min': 2.853495e-13,
  'rms_mean': 0.19007404,
  'rms_std': 0.078203216,
  'rms_kurtosis': -0.3229372143980327,
  'rms_skew': 0.5490007976

In [9]:
df_features = pd.DataFrame(all_features)

In [10]:
df_features.shape

(1055, 128)

In [11]:
df_features.head()

spectral_centroid_max  spectral_centroid_min  spectral_centroid_mean  \
0            6396.128033             758.085587             2497.847117   
1            5339.076724            1019.369702             2294.895607   
2            7254.064778             651.186826             2696.901485   
3            6140.674873               0.000000             2380.049677   
4            7199.257250            1020.574241             2826.380780   

   spectral_centroid_std  spectral_centroid_kurtosis  spectral_centroid_skew  \
0             778.458011                    4.642043                1.576085   
1             604.767987                    1.803070                0.943630   
2             880.376419                    2.895691                1.244553   
3             830.415212                    2.595801                1.385173   
4             876.072413                    6.361841                2.150542   

   spectral_rolloff_max  spectral_rolloff_min  spectral_rolloff_mean  \
0           9883.740234           1012.060547            5572.599637   
1           9130.078125           1722.656250            4914.999411   
2           9819.140625            861.328125            5974.730538   
3           9733.007812              0.000000            5374.324450   
4          10099.072266           2067.187500            5883.364424   

   spectral_rolloff_std  ...  mfcc_11_kurtosis  mfcc_11_skew  mfcc_12_max  \
0           1544.649657  ...         -0.149899     -0.098516    32.351917   
1           1341.457851  ...          0.120776     -0.207388    21.607838   
2           1598.705507  ...          0.024153      0.124245    27.043575   
3           1572.656797  ...         -0.120468     -0.165288    27.557299   
4           1748.422131  ...         -0.061357     -0.006184    16.286320   

   mfcc_12_min  mfcc_12_mean  mfcc_12_std  mfcc_12_kurtosis  mfcc_12_skew  \
0   -35.871353     -7.444573     8.756847          0.750816      0.385795   
1   -36.618702     -4.257775     9.034795         -0.080838      0.118976   
2   -37.588905     -5.011933     8.631045          0.385873     -0.008049   
3   -34.702950     -5.703769     9.205033          0.121554     -0.134600   
4   -45.887043    -14.256561     9.990096          0.160589      0.098548   

        tempo  label  
0  107.666016  forro  
1  143.554688  forro  
2  112.347147  forro  
3  107.666016  forro  
4  129.199219  forro  

[5 rows x 128 columns]

In [12]:
df_features.to_csv('./all_features_BR.csv', index=False)